<p><font size="5"><b>MAP VISUALIZATION OF COVID-19 SITUATION IN FRANCE </b></font></p>


<p><font size="4"><b> *PYTHON - FOLIUM*  
 - 02/01/2010* </b></font></p>

<p><font size="3"> *Source données :https://www.data.gouv.fr/fr/datasets/r/08c18e08-6780-452d-9b8c-ae244ad529b3* </font></p>

*© 2020, Gérald Bouget  (<mailto:geraldbouget@gmail.com>)


Visualisation sur Folium de la situation du Covid-19 en France en temps réel (mise à jour automatique de la base de données chaque jour sur www.data.gouv.fr).


- La première carte affiche les données par région des hospitalisations en cours  
- La deuxième carte affuche les données départementales des hospitalisation en cours  
- La troisième carte afiche les données des décés cumulés par département dus au covid-19 (hors Ehpad)  

In [2]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import datetime
import geopandas as gpd
import re
import os

In [10]:
# Chargement dataset
df_reg_age = pd.read_csv('https://www.data.gouv.fr/fr/datasets/r/08c18e08-6780-452d-9b8c-ae244ad529b3', sep=';')
df_reg_age.head()

reg  cl_age90        jour  hosp  rea  rad  dc
0    1         0  2020-03-18     0    0    0   0
1    1         9  2020-03-18     0    0    0   0
2    1        19  2020-03-18     0    0    0   0
3    1        29  2020-03-18     0    0    0   0
4    1        39  2020-03-18     0    0    0   0

In [16]:
# visualisation des hospitalisations en cours au niveau régional
def regions():
    #import csv hospitalisation en cours par region et par age
    df_reg_age = pd.read_csv('https://www.data.gouv.fr/fr/datasets/r/08c18e08-6780-452d-9b8c-ae244ad529b3', sep=';')
    #on garde que la ligne age ='0' car total des classes d'âge (faire inverse pour analyse par classes)
    df_reg_age = df_reg_age.query('cl_age90==0')
    #conversion colonne date en format date pandas
    df_reg_age.jour=pd.to_datetime(df_reg_age.jour)
    #selection de la date la plus récente pour photographie de l'ananlyse ponctuelle et groupby par région
    #et somme du nombre d'hospitalisations par région pour le jour le plus récent
    df_carte = df_reg_age[df_reg_age.jour==df_reg_age.jour.max()].groupby(['reg', 'jour']).hosp.sum().reset_index()
    
    
    #chargement coordonnées au format geojson pour régions françaises
    geojson_reg = gpd.read_file('https://france-geojson.gregoiredavid.fr/repo/regions.geojson')
    geojson_reg.code = geojson_reg.code.apply(lambda x: int(x))
    geojson_reg.nom = geojson_reg.nom.apply(lambda x: str(x))
    #merge fichier geojoson avec dataframe hospitalisation
    df_carte_merge = pd.merge(geojson_reg, df_carte.rename(columns={'reg':'code'}))
    #réorganisation des col (fonctionne mieux apparemment avec colonne geometry en dernier)
    df_carte_merge_data=df_carte_merge[['code','nom', 'hosp', 'jour', 'geometry']]
    df_carte_merge_data['jour'] = df_carte_merge_data['jour'].dt.strftime('%Y-%m-%d') #à faire car sinon folium ne va pas fonctionner
    
    
    m6 = folium.Map([47, 2.344467863359848], zoom_start=6)
    style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
    highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

    text = folium.features.GeoJson(
    df_carte_merge_data,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['hosp', 'jour', 'nom'],
        aliases=['Nombre d\'hospitalisations : ', 'Date :', 'Région :'],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)

    g=folium.Choropleth(
    geo_data=df_carte_merge_data,
    name='choropleth',
    data=df_carte_merge_data,
    columns=["code","hosp"],
    key_on="feature.properties.code", #cle de jointure entre fichier geojson et fichier data
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Hospitalisations en cours par region",
    highlight=True,
    overlay=True
).add_to(m6)

    m6.add_child(text)
    m6.keep_in_front(text)
    folium.LayerControl().add_to(m6)
#m2.save(os.path.join('results', 'carte2b.html'))


    return m6

In [17]:
regions()

In [25]:
# visualisation des hospitalisations en cours au niveau départemental 
def departements():
    #import csv hospitalisation en cours par region et par age
    df_dep_sex = pd.read_csv('https://www.data.gouv.fr/fr/datasets/r/63352e38-d353-4b54-bfd1-f1b3ee1cabd7', sep=';')
    #on garde que la ligne age ='0' car total des classes d'âge (faire inverse pour analyse par classes)
    df_dep_sex = df_dep_sex.query('sexe==0')
    #conversion colonne date en format date pandas
    df_dep_sex.jour=pd.to_datetime(df_dep_sex.jour)
    #selection de la date la plus récente pour photographie de l'ananlyse ponctuelle et groupby par région
    #et somme du nombre d'hospitalisations par région pour le jour le plus récent
    df_carte = df_dep_sex[df_dep_sex.jour==df_dep_sex.jour.max()].groupby(['dep', 'jour']).hosp.sum().reset_index()
    
    
    #chargement coordonnées au format geojson pour régions françaises
    geojson_dep = gpd.read_file('https://france-geojson.gregoiredavid.fr/repo/departements.geojson')
    geojson_dep.code = geojson_dep.code.apply(lambda x: str(x))
    geojson_dep.nom = geojson_dep.nom.apply(lambda x: str(x))
    #merge fichier geojoson avec dataframe hospitalisation
    df_carte_merge = pd.merge(geojson_dep, df_carte.rename(columns={'dep':'code'}))
    #réorganisation des col (fonctionne mieux apparemment avec colonne geometry en dernier)
    df_carte_merge_data=df_carte_merge[['code','nom', 'hosp', 'jour', 'geometry']]
    df_carte_merge_data['jour'] = df_carte_merge_data['jour'].dt.strftime('%Y-%m-%d') #à faire car sinon folium ne va pas fonctionner
    
    
    m = folium.Map([47, 2.344467863359848], zoom_start=6)
    style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
    highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

    text = folium.features.GeoJson(
    df_carte_merge_data,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['hosp','jour', 'nom'],
        aliases=['Nombre d\'hospitalisations : ', 'Date :', 'Département : '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)

    g=folium.Choropleth(
    geo_data=df_carte_merge_data,
    name='choropleth',
    data=df_carte_merge_data,
    columns=["code","hosp"],
    key_on="feature.properties.code", #cle de jointure entre fichier geojson et fichier data
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Hosp. en cours par departement',
    highlight=True,
    overlay=True
).add_to(m)

    m.add_child(text)
    m.keep_in_front(text)
    folium.LayerControl().add_to(m)
#m2.save(os.path.join('results', 'carte2b.html'))


    return m

In [26]:
departements()

In [27]:
#visualisation décés au niveau départemental
def dc_dep():
    #import csv hospitalisation en cours par region et par age
    df_dep_sex = pd.read_csv('https://www.data.gouv.fr/fr/datasets/r/6fadff46-9efd-4c53-942a-54aca783c30c', sep=';')
    #on garde que la ligne age ='0' car total des classes d'âge (faire inverse pour analyse par classes)
    #df_dep_sex = df_dep_sex[df_dep_sex.sexe==0]
    #conversion colonne date en format date pandas
    df_dep_sex.jour=pd.to_datetime(df_dep_sex.jour)
    #selection de la date la plus récente pour photographie de l'ananlyse ponctuelle et groupby par région
    #et somme du nombre d'hospitalisations par région pour le jour le plus récent
    df_carte = df_dep_sex.groupby(['dep']).incid_dc.sum()
    #garder mode df
    df_carte=df_carte.to_frame()
    df_carte.reset_index(inplace=True)
    
    #chargement coordonnées au format geojson pour régions françaises
    geojson_dep = gpd.read_file('https://france-geojson.gregoiredavid.fr/repo/departements.geojson')
    geojson_dep.code = geojson_dep.code.apply(lambda x: str(x))
    geojson_dep.nom = geojson_dep.nom.apply(lambda x: str(x))
   
    #merge fichier geojoson avec dataframe hospitalisation
    df_carte_merge = pd.merge(geojson_dep, df_carte.rename(columns={'dep':'code'}))
    #réorganisation des col (fonctionne mieux apparemment avec colonne geometry en dernier)
    df_carte_merge_data=df_carte_merge[['code','nom', 'incid_dc', 'geometry']]
    
    
    
    m = folium.Map([47, 2.344467863359848], zoom_start=6)
    style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
    highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

    text = folium.features.GeoJson(
    df_carte_merge_data,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['incid_dc', 'nom'],
        aliases=['Nombre décés cumulés : ', 'Département : '],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)

    g=folium.Choropleth(
    geo_data=df_carte_merge_data,
    name='choropleth',
    data=df_carte_merge_data,
    columns=["code","incid_dc"],
    key_on="feature.properties.code", #cle de jointure entre fichier geojson et fichier data
    fill_color='PuBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name= f"Nbr deces cumules par dep au {df_dep_sex.iloc[-1,1].strftime('%d %B %Y')}.",
    highlight=True,
    overlay=True
).add_to(m)

    m.add_child(text)
    m.keep_in_front(text)
    folium.LayerControl().add_to(m)
    #m.save(os.path.join('results', 'dc_dep.html'))


    return m

In [28]:
dc_dep()